# Import libraries

In [1]:
import sys
from pathlib import Path
sys.path.insert(0,'..')
import glob
#!pip install openpyxl

In [3]:
import os
import sys
import pandas as pd
import numpy as np
import pickle
import matplotlib.pyplot as plt
import h5py
import re

from functools import partial
from multiprocessing import Pool

from lhcsmapi.Time import Time
from lhcsmapi.metadata import signal_metadata
from lhcsmapi.pyedsl.dbsignal.post_mortem.PmDbRequest import PmDbRequest
from lhcsmapi.analysis.RbCircuitQuery import RbCircuitQuery

from src.acquisitions.current_voltage_diode_leads_nxcals import CurrentVoltageDiodeLeadsNXCALS
from src.acquisitions.current_voltage_diode_leads_pm import CurrentVoltageDiodeLeadsPM
from src.acquisitions.ee_t_res_pm import EETResPM
from src.acquisitions.ee_u_dump_res_pm import EEUDumpResPM
from src.acquisitions.leads import Leads
from src.acquisitions.pc_pm import PCPM
from src.acquisitions.qh_pm import QHPM
from src.acquisitions.voltage_logic_iqps import VoltageLogicIQPS
from src.acquisitions.voltage_nqps import VoltageNQPS
from src.acquisitions.voltage_nxcals import VoltageNXCALS

from src.utils.utils import log_acquisition
from src.utils.hdf_tools import acquisition_to_hdf5, load_from_hdf_with_regex
from src.utils.mp3_excel_processing import get_fgc_timestamp, get_fgc_timestamp_missing

ModuleNotFoundError: No module named 'lhcsmapi'

# Read the (clean) MP3 file

In [ ]:
mp3_fpa_df_raw = pd.read_excel("../data/RB_TC_extract_2021_11_22.xlsx")
len(mp3_fpa_df_raw)

In [ ]:
# First row contains units, 9 rows contain only "Before Notebooks" and "After Notebooks" information, which need to be droped
mp3_fpa_df = mp3_fpa_df_raw.dropna(subset = ['Date (FGC)', 'Circuit Name'])
mp3_fpa_df_raw.iloc[~mp3_fpa_df_raw.index.isin(mp3_fpa_df.index)] #show droped rows

# Find FGC timestamp for each FPA event in MP3 excel

In [6]:
mp3_fpa_df['timestamp_fgc'] = mp3_fpa_df.apply(get_fgc_timestamp, axis=1)


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


# Find missing fgc timestamps in mp3 file

In [7]:
# some fgc timestamps have wrong hours
mp3_fpa_df_primary_missing = mp3_fpa_df[(mp3_fpa_df.timestamp_fgc.isna()) & (mp3_fpa_df['Nr in Q event'] == 1)]
mp3_fpa_df_primary_missing['timestamp_fgc'] = mp3_fpa_df_primary_missing.apply(get_fgc_timestamp_missing, axis=1)
found_fgc_timestamps_df = mp3_fpa_df_primary_missing["timestamp_fgc"].dropna()
mp3_fpa_df.loc[found_fgc_timestamps_df.index, "timestamp_fgc"] = mp3_fpa_df_primary_missing["timestamp_fgc"].dropna().values


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [8]:
print(f"{len(mp3_fpa_df)} unique fgc events") # 841 Primary quenches?
print(f"{len(mp3_fpa_df[mp3_fpa_df['Nr in Q event']==1])} mp3 primary quench entries") # 834 primary quenches with correct notes

4399 unique fgc events
918 mp3 primary quench entries


# Select events to download

In [9]:
mp3_fpa_df_unique = mp3_fpa_df.drop_duplicates(subset=['timestamp_fgc', 'Circuit Name'])

In [10]:
# Time.to_string(1514761200000000000), Time.to_unix_timestamp('2018-01-01 00:00:00+01:00')
mp3_fpa_df_period = mp3_fpa_df_unique[mp3_fpa_df_unique['timestamp_fgc'] >= 1388530800000000000].reset_index(drop=True) 
len(mp3_fpa_df_period)

828

In [3]:
signal_groups = [PCPM, VoltageNXCALS, VoltageNQPS, VoltageLogicIQPS, EEUDumpResPM, QHPM]
file_dir = Path('/eos/project/m/ml-for-alarm-system/private/RB_signals')
signal_groups = [VoltageNQPS]

## Test query

In [4]:
context_path = file_dir / "data_test"
fpa_identifier = {'circuit_type': 'RB',
                 'circuit_name': 'RB.A78',
                 'timestamp_fgc': 1616962174400000000}

In [14]:
for signal_group in signal_groups:
    group = signal_group(**fpa_identifier)#, spark=spark)
    acquisition_to_hdf5(acquisition=group, 
                        file_dir=file_dir, 
                        context_dir_name="context_test",
                        failed_queries_dir_name="failed_test",
                        data_dir_name="data_test")
        
log_acquisition(identifier=fpa_identifier, log_data={"download_complete": True}, log_path=context_path)

	Querying PM event timestamps for system: QPS, className: DQAMGNSRB_PMREL, source: * from 2021-03-28 22:09:24.400 to 2021-03-28 22:16:14.400


## Load data

In [5]:
file_name = f"{fpa_identifier['circuit_type']}_{fpa_identifier['circuit_name']}_{fpa_identifier['timestamp_fgc']}.hdf5"
file_path = file_dir / Path('data_test') / file_name

signals = ['I_MEAS','VoltageNQPS.*U_DIODE','VoltageNXCALS.*U_DIODE','I_EARTH_PCNT', 'IEARTH.I_EARTH','U_QS0','U_1','U_2','I_HDS', 'U_HDS','EEUDumpResPM']
signals = ['VoltageNQPS.*U_DIODE']
len(signals)

1

In [6]:
def get_hdf_tree(file_path: Path, regex_list: list = ['']):
    """
    get paths of datasets in hdf file which contain regex
    :param file_path: path of the hdf file to extract file tree
    :param regex_list: list of strings which file should contain
    : return: list of paths with regex in hdf5 file
    """

    def extract_file_tree(name, node):
        """
        append parent path of hdf dataset file
        :param name: name of dataset
        :param node: node of dataset
        """
        if isinstance(node, h5py.Dataset):
            parent_path = str(Path(name).parent)
            if not parent_path in file_tree:
                file_tree.append(parent_path)
        return None

    with h5py.File(file_path, "r") as f:
        file_tree = []
        f.visititems(extract_file_tree)
        file_tree_filtered = [t for t in file_tree for r in regex_list if r in t]

    return file_tree_filtered


def load_from_hdf_with_regex(file_path: Path, regex_list: list = ['']) -> list:
    """
    get datasets in hdf file which contain regex
    :param file_path: path of the hdf file to extract file tree
    :param regex_list: list of strings which file should contain
    : return: list of DataFrames with data of regex
    """
    hdf_paths = get_hdf_tree(file_path=file_path, regex_list=regex_list)
    data = []
    for hdf_path in hdf_paths:
        data.append(hdf_to_df(file_path=file_path, hdf_dir=hdf_path))
    return data

In [7]:
from src.utils.hdf_tools import hdf_to_df

In [9]:
hdf_paths = get_hdf_tree(file_path=file_path)
len(hdf_paths)

161

In [10]:
hdf_paths

['PCPM/IAB.I_A',
 'PCPM/IEARTH.I_EARTH',
 'PCPM/STATUS.I_EARTH_PCNT',
 'PCPM/STATUS.I_MEAS',
 'PCPM/STATUS.I_REF',
 'PCPM/STATUS.V_MEAS',
 'PCPM/STATUS.V_REF',
 'VoltageNQPS/MB.A10L8:U_DIODE_RB',
 'VoltageNQPS/MB.A10R7:U_DIODE_RB',
 'VoltageNQPS/MB.A11L8:U_DIODE_RB',
 'VoltageNQPS/MB.A11R7:U_DIODE_RB',
 'VoltageNQPS/MB.A12L8:U_DIODE_RB',
 'VoltageNQPS/MB.A12R7:U_DIODE_RB',
 'VoltageNQPS/MB.A13L8:U_DIODE_RB',
 'VoltageNQPS/MB.A13R7:U_DIODE_RB',
 'VoltageNQPS/MB.A14L8:U_DIODE_RB',
 'VoltageNQPS/MB.A14R7:U_DIODE_RB',
 'VoltageNQPS/MB.A15L8:U_DIODE_RB',
 'VoltageNQPS/MB.A15R7:U_DIODE_RB',
 'VoltageNQPS/MB.A16L8:U_DIODE_RB',
 'VoltageNQPS/MB.A16R7:U_DIODE_RB',
 'VoltageNQPS/MB.A17L8:U_DIODE_RB',
 'VoltageNQPS/MB.A17R7:U_DIODE_RB',
 'VoltageNQPS/MB.A18L8:U_DIODE_RB',
 'VoltageNQPS/MB.A18R7:U_DIODE_RB',
 'VoltageNQPS/MB.A19L8:U_DIODE_RB',
 'VoltageNQPS/MB.A19R7:U_DIODE_RB',
 'VoltageNQPS/MB.A20L8:U_DIODE_RB',
 'VoltageNQPS/MB.A20R7:U_DIODE_RB',
 'VoltageNQPS/MB.A21L8:U_DIODE_RB',
 'VoltageNQP

In [ ]:
data = []
for hdf_path in hdf_paths:
    data.append(hdf_to_df(file_path=file_path, hdf_dir=hdf_path))

In [ ]:
data = load_from_hdf_with_regex(file_path)

In [ ]:
fig = plt.figure(figsize=(20, 15))
for i, s in enumerate(signals):
    fig.add_subplot(4, 3, i+1)
    n_signals = 0
    for df in data:
        if bool(re.search(s, df.columns.values[0])):
            plt.plot(df.index.values, df.values)
            n_signals += 1
    plt.title(f"{s} ({n_signals})")
plt.show()

## Query all FGC events

In [ ]:
Time.to_unix_timestamp('2018-01-01 00:00:00+01:00')

In [ ]:
# Time.to_string(1514761200000000000), Time.to_unix_timestamp('2018-01-01 00:00:00+01:00')
mp3_fpa_df_period = mp3_fpa_df_unique[mp3_fpa_df_unique['timestamp_fgc'] >= 1388530800000000000].reset_index(drop=True) 
len(mp3_fpa_df_period)

In [ ]:
for index, row in mp3_fpa_df_period.iterrows():
    fpa_identifier = {'circuit_type': row['Circuit Family'],
                      'circuit_name': row['Circuit Name'],
                      'timestamp_fgc': int(row['timestamp_fgc'])}
    file_name = f"{fpa_identifier['circuit_type']}_{fpa_identifier['circuit_name']}_{fpa_identifier['timestamp_fgc']}.hdf5"

    for signal_group in signal_groups:
        group = signal_group(**fpa_identifier, spark=spark)
        acquisition_to_hdf5(acquisition=group, 
                            file_dir=file_dir,
                            context_dir_name="20220624_context",
                            failed_queries_dir_name="20220624_failed",
                            data_dir_name="20220624_data")

    log_acquisition(identifier=fpa_identifier, log_data={"download_complete": True}, log_path=context_path)
    
    file_path = file_dir / Path('20220624_data') / file_name
    data = load_from_hdf_with_regex(file_path)
    fig = plt.figure(figsize=(20, 15))
    for i, s in enumerate(signals):
        fig.add_subplot(4, 3, i+1)
        n_signals = 0
        for df in data:
            if bool(re.search(s, df.columns.values[0])):
                plt.plot(df.index.values, df.values)
                n_signals += 1
        plt.title(f"{s} ({n_signals})")
    plt.savefig(str(file_dir / Path('20220624_plots') / f"{fpa_identifier['circuit_type']}_{fpa_identifier['circuit_name']}_{fpa_identifier['timestamp_fgc']}.png"))

	Querying PM event signal(s) STATUS.I_MEAS, IAB.I_A, IEARTH.IEARTH, STATUS.I_EARTH_PCNT, STATUS.I_REF for system: FGC, className: 51_self_pmd, source: RPTE.UA23.RB.A12 at 2014-12-11 21:45:14.580
	Querying NXCALS signal(s) MB.A8R1:U_DIODE_RB, MB.B8R1:U_DIODE_RB, MB.A9R1:U_DIODE_RB, MB.B9R1:U_DIODE_RB, MB.A10R1:U_DIODE_RB... from 2014-12-11 21:44:24.580 to 2014-12-11 21:53:34.580
	Querying NXCALS signal(s) MB.A8R1:U_EARTH_RB, MB.B8R1:U_EARTH_RB, MB.A10R1:U_EARTH_RB, MB.B11R1:U_EARTH_RB, MB.C12R1:U_EARTH_RB... from 2014-12-11 21:44:24.580 to 2014-12-11 21:53:34.580
	Querying PM event timestamps for system: QPS, className: DQAMGNSRB_PMREL, source: * from 2014-12-11 21:45:04.580 to 2014-12-11 21:51:54.580
	Querying PM event timestamps for system: QPS, className: DQAMCNMB_PMSTD, source: * from 2014-12-11 21:45:04.580 to 2014-12-11 21:45:24.580


Post Mortem returned no data for the following query: http://pm-api-pro/v2//pmdata/header/within/duration?system=QPS&className=DQAMGNSRB_PMREL&source=*&fromTimestampInNanos=1418330704580000000&durationInNanos=410000000000
Some nQPS PM buffers missing. ['B8R1', 'B9R1', 'B10R1', 'B11R1', 'B12R1', 'B13R1', 'B14R1', 'B15R1', 'B16R1', 'B17R1', 'B18R1', 'B19R1', 'B20R1', 'B21R1', 'B22R1', 'B23R1', 'B24R1', 'B25R1', 'B26R1', 'B27R1', 'B28R1', 'B29R1', 'B30R1', 'B31R1', 'B32R1', 'B33R1', 'B34R1', 'B34L2', 'B33L2', 'B32L2', 'B31L2', 'B30L2', 'B29L2', 'B28L2', 'B27L2', 'B26L2', 'B25L2', 'B24L2', 'B23L2', 'B22L2', 'B21L2', 'B20L2', 'B19L2', 'B18L2', 'B17L2', 'B16L2', 'B15L2', 'B14L2', 'B13L2', 'B12L2', 'B11L2', 'B10L2', 'B9L2', 'B8L2'] not found for RB.A12 within [(10, 's'), (400, 's')] around 1418330714580000000.


Querying PM:   0%|          | 0/2 [00:00<?, ?it/s]

Querying iQPS logic PM:   0%|          | 0/2 [00:00<?, ?it/s]

	Querying PM event timestamps for system: QPS, className: DQAMSNRB, source: RR17.RB.A12 from 2014-12-11 21:45:04.580 to 2014-12-11 22:01:54.580
	Querying PM event timestamps for system: QPS, className: DQAMSNRB, source: UA23.RB.A12 from 2014-12-11 21:45:04.580 to 2014-12-11 22:01:54.580
	Querying PM event signal(s) RR17.RB.A12:U_DUMP_RES for system: QPS, className: DQAMSNRB, source: RR17.RB.A12 at 2014-12-11 21:45:14.877
	Querying PM event signal(s) UA23.RB.A12:U_DUMP_RES for system: QPS, className: DQAMSNRB, source: UA23.RB.A12 at 2014-12-11 21:45:15.124
	Querying PM event timestamps for system: QPS, className: DQAMCNMB_PMHSU, source: * from 2014-12-11 21:45:04.580 to 2014-12-11 21:53:34.580


...

Querying iQPS logic PM:   0%|          | 0/2 [00:00<?, ?it/s]

	Querying PM event timestamps for system: QPS, className: DQAMSNRB, source: UJ33.RB.A34 from 2016-12-06 04:29:21.240 to 2016-12-06 04:46:11.240
	Querying PM event timestamps for system: QPS, className: DQAMSNRB, source: UA43.RB.A34 from 2016-12-06 04:29:21.240 to 2016-12-06 04:46:11.240
	Querying PM event signal(s) UJ33.RB.A34:U_DUMP_RES for system: QPS, className: DQAMSNRB, source: UJ33.RB.A34 at 2016-12-06 04:29:31.555
	Querying PM event signal(s) UA43.RB.A34:U_DUMP_RES for system: QPS, className: DQAMSNRB, source: UA43.RB.A34 at 2016-12-06 04:29:31.776
	Querying PM event timestamps for system: QPS, className: DQAMCNMB_PMHSU, source: * from 2016-12-06 04:29:21.240 to 2016-12-06 04:37:51.240


Querying PM:   0%|          | 0/6 [00:00<?, ?it/s]


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.h


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.h

In [ ]:
file_dir